In [9]:
import os
import numpy as np 
import pandas as pd 
import tensorflow as tf
import keras
import matplotlib.pyplot as plt

In [115]:
# Data info 
rootDir = '..your_data_path/'

Dataset = 'NCLT'
TrainOrTest = '/Train/'
SequenceDate = '2012-01-15'

SCImiddlePath = '/5. SCI_jet0to15_BackAug/'

GridCellSize = '10'

In [116]:
DataPath = rootDir + Dataset + TrainOrTest + SequenceDate + SCImiddlePath + GridCellSize + '/'
print(DataPath)

/media/gskim/IRAP-ADV1/Data/ICRA2019/NCLT/Train/2012-01-15/5. SCI_jet0to15_BackAug/10/


In [181]:
def getTrainingDataNCLT(DataPath, SequenceDate):    

    # info
    WholeData = os.listdir(DataPath)
    nWholeData = len(WholeData)
    print(str(nWholeData) + ' data exist in ' + SequenceDate)
    
    # read 
    X = []
    y = []
    for ii in range(nWholeData):
        dataName = WholeData[ii]
        dataPath = DataPath + dataName
        
        dataTrajNodeOrder = int(dataName[0:5])

        SCI = plt.imread(dataPath)
        dataPlaceIndex = int(dataName[6:11])
        
        X.append(SCI)
        y.append(dataPlaceIndex)
        
        # progress message 
        if ii%1000==0:
            print(str(format((ii/nWholeData)*100, '.1f')), '% loaded.')
        
        
    dataShape = SCI.shape
    
    # X
    X_nd = np.zeros(shape=(nWholeData, dataShape[0], dataShape[1], dataShape[2]))
    for jj in range(len(X)):
        X_nd[jj, :, :] = X[jj]
    X_nd = X_nd.astype('float32')
    
    # y (one-hot encoded)
    from sklearn.preprocessing import LabelEncoder
    lbl_enc = LabelEncoder()
    lbl_enc.fit(y)
    
    ClassesTheSequenceHave = lbl_enc.classes_
    nClassesTheSequenceHave = len(ClassesTheSequenceHave)
    
    y = lbl_enc.transform(y)
    y_nd = keras.utils.np_utils.to_categorical(y, num_classes=nClassesTheSequenceHave)

    # log message 
    print('Data size: %s' % nWholeData)
    print(' ')
    print('Data shape:', X_nd.shape)
    print('Label shape:', y_nd.shape)
    
    return X_nd, y_nd, lbl_enc
    

In [182]:
[X, y, lbl_enc] = getTrainingDataNCLT(DataPath, SequenceDate)

15078 data exist in 2012-01-15
0.0 % loaded.
6.6 % loaded.
13.3 % loaded.
19.9 % loaded.
26.5 % loaded.
33.2 % loaded.
39.8 % loaded.
46.4 % loaded.
53.1 % loaded.
59.7 % loaded.
66.3 % loaded.
73.0 % loaded.
79.6 % loaded.
86.2 % loaded.
92.9 % loaded.
99.5 % loaded.
Data size: 15078
Data shape: (15078, 40, 120, 3)
Label shape: (15078, 579)


In [172]:
dataShape = X[0].shape
labelShape = y[0].shape

print(dataShape)
print(labelShape)

(40, 120, 3)
(579,)


In [173]:
# Model 
from keras import backend as K
K.clear_session()

ModelName = 'my_model'

Drop1 = 0.7
Drop2 = 0.7

KernelSize = 5

nConv1Filter = 64
nConv2Filter = 128
nConv3Filter = 256

nFCN1 = 64

inputs = keras.layers.Input(shape=(dataShape[0], dataShape[1], dataShape[2]))
x = keras.layers.Conv2D(filters=nConv1Filter, kernel_size=KernelSize, activation='relu', padding='same')(inputs)
x = keras.layers.MaxPooling2D(pool_size=(2, 2), strides=None, padding='valid')(x)
x = keras.layers.BatchNormalization()(x)
x = keras.layers.Conv2D(filters=nConv2Filter, kernel_size=KernelSize, activation='relu', padding='same')(x)
x = keras.layers.MaxPool2D()(x)
x = keras.layers.BatchNormalization()(x)
x = keras.layers.Conv2D(filters=nConv3Filter, kernel_size=KernelSize, activation='relu', padding='same')(x)
x = keras.layers.MaxPool2D()(x)
x = keras.layers.Flatten()(x)
x = keras.layers.Dropout(rate=Drop1)(x)
x = keras.layers.Dense(units=nFCN1)(x)
x = keras.layers.Dropout(rate=Drop2)(x)
outputs = keras.layers.Dense(units=labelShape[0], activation='softmax')(x)

model = keras.models.Model(inputs=inputs, outputs=outputs)

In [174]:
# Model Compile 
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['acc'])
model.build(None,)

In [1]:
#Train
X_train = X
y_train = y

nEpoch = 200

model.fit(X_train,
          y_train,
          epochs=nEpoch,
          batch_size=64,
          verbose=1
         )

In [2]:
#Train
X_train = X
y_train = y

nEpoch = 200

model.fit(X_train,
          y_train,
          epochs=nEpoch,
          batch_size=64,
          verbose=1
         )

In [186]:
# model save 
modelName = 'ModelWS_' + GridCellSize + 'm_' + ModelName + '.h5'
model.save(modelName)
